# Pre-processing the ERS error messages and Run metadata in 2023

Most of the cells in what follows are not really needed to be re-executed, but show the usual process.

In [1]:
# From this page: https://atlasop.cern.ch/tdaq/ers/en-US/static/app/ers/ers.html
# We can export the messages we're interested in. 
# In this case I filtered all the ERS messages (of the ATLAS partition) with severity !INFO of 2023, with:
# - AppID: CHIP-ATLAS
# - MessageID: *TestFailed*
# - Msg Text filter: *tpu*

import pandas as pd
import re
from datetime import datetime
import pytz

ers_folder = "/eos/user/j/jhoya/DAQ/AnomalyDetection/strada/dataset_generation/ers_errors/"
#df = pd.read_csv('/eos/user/j/jhoya/DAQ/AnomalyDetection/strada/dataset_generation/ers_errors/tpu-failures-2023-andrei.csv')
df = pd.read_csv(f'{ers_folder}2023_ERS_CHIP_TestFailed_tpu.csv')


# Extract the TPU number from the 'text' column
def extract_tpu(text):
    #match = re.search(r"tpu-[a-zA-Z0-9-]+:pc-tdq-tpu-(\d+)", text)
    match = re.search(r"pc-tdq-tpu-(\d+)", text)
    return match.group(1) if match else None

# Extract the failure source from the 'text' column
def extract_failure_source(text):
    #match = re.search(r"Component: ([^:]+):HLT", text)
    #match = re.search(r"Test failure for application: ([^:]+):HLT", text)
    match = re.search(r"Test failure for application: ([^:]+)", text)
    return match.group(1) if match else None


# Convert 'time' to Europe/Berlin timezone. This is really annoying, but needed if we start using this in LCRC...
def convert_to_cern_timezone(time_str):

    time_format = "%H:%M:%S %b %d %Y"
    
    # Convert the time string to a datetime object
    naive_dt = datetime.strptime(time_str, time_format)
    
    # Assign UTC timezone
    utc_timezone = pytz.timezone('UTC')
    utc_dt = utc_timezone.localize(naive_dt)
    
    # Convert the UTC datetime to Europe/Berlin timezone
    cern_timezone = pytz.timezone('Europe/Berlin')
    cern_dt = utc_dt.astimezone(cern_timezone)
    
    return cern_dt


# Create the new columns
df['tpu_number'] = df['text'].apply(extract_tpu)
df['failure_source'] = df['text'].apply(extract_failure_source)


# Convert to Europe/Berlin timezone
df['time_cern'] = df['time'].apply(convert_to_cern_timezone)

# Keep only the columns we want: 'time', 'utime', 'tpu_number', and 'failure_source'
df_processed = df[['time_cern', 'utime', 'tpu_number', 'failure_source']]

# Group by 'time', 'utime', and 'tpu_number', and concatenate 'failure_source' values. Otherwise we get a lot of rows for the same time and with 1 is enough. Keep the information in case we want to understand more what's the issue.
df_merged = df_processed.groupby(['time_cern', 'utime', 'tpu_number']).agg({
    'failure_source': lambda x: '; '.join(x.dropna().unique())  # Merge unique failure sources
}).reset_index()

df_merged.to_csv(f"{ers_folder}processed_2023_ERS.csv", index=False)


In [27]:
# Now we want to know all the available runs in 2023. For this we use the file: ""../../../datasets/atlas-data-summary-runs-2023.html"

###### Important note. If you want to use this, you'll need to change the configuration of this SWAN session and add a configuration script. You should use for exaple:
###### /eos/user/j/jhoya/DAQ/AnomalyDetection/strada/setup_lxplus.sh   -> We need TDAQ release to use beauty

import argparse
import sys
import datetime as dt
import json

import numpy as np
import pandas as pd

sys.path.append('/eos/user/j/jhoya/DAQ/AnomalyDetection/strada/detection_combined/')

from utils.offlinepbeastdataloader import OfflinePBeastDataLoader



offline_pbeast_data_loader = OfflinePBeastDataLoader('/eos/user/j/jhoya/DAQ/AnomalyDetection/strada/datasets/atlas-data-summary-runs-2023.html')
run_numbers = offline_pbeast_data_loader.get_run_numbers()
runs_amount = offline_pbeast_data_loader.__len__()

df_runs = offline_pbeast_data_loader.get_runs_df()
    
print(runs_amount, run_numbers)


123 [461096, 461002, 460945, 460944, 460916, 460913, 460860, 460837, 460493, 460477, 460447, 460438, 460436, 460348, 460009, 456749, 456729, 456714, 456685, 456665, 456522, 456409, 456386, 456346, 456316, 456314, 456303, 456273, 456225, 456164, 456151, 456126, 456118, 456110, 456016, 455975, 455924, 455899, 455870, 455857, 455838, 455837, 455818, 455814, 455795, 455702, 455623, 455589, 454322, 454222, 454188, 454163, 454129, 454083, 454054, 453981, 453858, 453816, 453795, 453754, 453733, 453713, 453657, 453644, 453617, 453556, 453530, 453353, 453319, 452872, 452843, 452799, 452787, 452785, 452726, 452696, 452669, 452640, 452624, 452573, 452533, 452463, 452266, 452241, 452202, 452163, 452028, 451936, 451896, 451866, 451804, 451794, 451735, 451618, 451611, 451595, 451587, 451569, 451557, 451543, 451295, 451140, 451094, 451063, 451046, 451037, 451022, 450997, 450894, 450518, 450445, 450427, 450360, 450271, 450227, 448990, 448984, 448982, 448715, 448637, 448546, 448543, 448519]


In [28]:
# Start, end and duration for each of the runs in 2023
df_runs

start                 end  duration
Run Number                                                  
461096     2023-09-19 22:16:00 2023-09-20 08:37:00       610
461002     2023-09-18 17:12:00 2023-09-19 10:23:00      1037
460945     2023-09-18 01:18:00 2023-09-18 06:53:00       305
460944     2023-09-17 15:51:00 2023-09-18 01:08:00       549
460916     2023-09-17 07:15:00 2023-09-17 09:13:00        61
460913     2023-09-16 19:45:00 2023-09-17 06:58:00       671
460860     2023-09-15 13:59:00 2023-09-16 10:21:00      1220
460837     2023-09-14 21:12:00 2023-09-15 07:43:00       610
460493     2023-09-11 07:05:00 2023-09-11 15:16:00       488
460477     2023-09-10 17:19:00 2023-09-11 03:15:00       549
460447     2023-09-10 06:51:00 2023-09-10 15:09:00       488
460438     2023-09-09 21:48:00 2023-09-10 00:09:00       122
460436     2023-09-09 10:22:00 2023-09-09 21:35:00       671
460348     2023-09-07 13:12:00 2023-09-08 04:17:00       915
460009     2023-09-01 07:53:00 2023-09-01 16:26:00       488
456749     2023-07-16 23:25:00 2023-07-17 01:06:00        61
456729     2023-07-16 08:46:00 2023-07-16 22:33:00       793
456714     2023-07-15 16:59:00 2023-07-16 07:01:00       854
456685     2023-07-15 05:46:00 2023-07-15 10:02:00       244
456665     2023-07-14 20:36:00 2023-07-15 04:02:00       427
456522     2023-07-14 08:50:00 2023-07-14 10:53:00       122
456409     2023-07-12 18:42:00 2023-07-13 15:53:00      1281
456386     2023-07-12 11:48:00 2023-07-12 16:58:00       305
456346     2023-07-11 23:57:00 2023-07-12 04:05:00       244
456316     2023-07-11 12:16:00 2023-07-11 21:53:00       549
456314     2023-07-11 11:10:00 2023-07-11 12:02:00        52
456303     2023-07-11 08:12:00 2023-07-11 09:43:00        61
456273     2023-07-10 23:22:00 2023-07-11 06:24:00       427
456225     2023-07-10 12:35:00 2023-07-10 20:09:00       427
456164     2023-07-09 20:03:00 2023-07-10 05:44:00       549
456151     2023-07-09 12:17:00 2023-07-09 17:59:00       305
456126     2023-07-08 20:45:00 2023-07-09 11:13:00       854
456118     2023-07-08 05:13:00 2023-07-08 19:45:00       854
456110     2023-07-07 11:37:00 2023-07-08 03:55:00       976
456016     2023-07-06 02:19:00 2023-07-06 16:16:00       793
455975     2023-07-05 10:17:00 2023-07-06 01:09:00       854
455924     2023-07-04 17:32:00 2023-07-05 08:18:00       854
455899     2023-07-03 18:06:00 2023-07-04 16:02:00      1281
455870     2023-07-03 01:11:00 2023-07-03 06:27:00       305
455857     2023-07-02 17:39:00 2023-07-02 23:31:00       305
455838     2023-07-02 06:10:00 2023-07-02 12:02:00       305
455837     2023-07-02 04:12:00 2023-07-02 05:53:00        61
455818     2023-07-01 19:22:00 2023-07-01 23:56:00       244
455814     2023-07-01 17:59:00 2023-07-01 19:16:00        61
455795     2023-07-01 01:30:00 2023-07-01 16:46:00       915
455702     2023-06-30 08:16:00 2023-06-30 23:17:00       915
455623     2023-06-28 20:42:00 2023-06-29 23:24:00        61
455589     2023-06-28 09:38:00 2023-06-28 20:14:00       610
454322     2023-06-12 23:15:00 2023-06-13 11:09:00       671
454222     2023-06-11 23:16:00 2023-06-12 11:11:00       671
454188     2023-06-11 12:32:00 2023-06-11 21:33:00       549
454163     2023-06-10 23:13:00 2023-06-11 10:57:00       671
454129     2023-06-10 06:42:00 2023-06-10 19:36:00       732
454083     2023-06-09 07:52:00 2023-06-10 05:20:00      1281
454054     2023-06-08 18:31:00 2023-06-09 04:38:00       610
453981     2023-06-07 22:22:00 2023-06-08 13:51:00       915
453858     2023-06-07 00:03:00 2023-06-07 11:23:00       671
453816     2023-06-06 03:36:00 2023-06-06 22:00:00      1098
453795     2023-06-05 11:49:00 2023-06-06 01:11:00       793
453754     2023-06-04 20:20:00 2023-06-05 10:11:00       793
453733     2023-06-04 13:24:00 2023-06-04 19:21:00       305
453713     2023-06-03 21:46:00 2023-06-04 12:12:00       854
453657     2023-06-03 14:10:00 2023-06-03 16:23:00       122
453644     2023-06-03 01:23:00 2023-06-03 13:04:00       671

In [21]:
# Use this only to get a DataFrame with the information. For a JSON file look below.

ers_folder = "/eos/user/j/jhoya/DAQ/AnomalyDetection/strada/dataset_generation/ers_errors/"
df_ers = pd.read_csv(f"{ers_folder}processed_2023_ERS.csv", parse_dates=True)


# Convert time columns to datetime format. Dates in python are a painnnnnn!!!
df_ers['time_cern'] = pd.to_datetime(df_ers['time_cern'], utc=True, errors='coerce').dt.tz_localize(None)
df_runs['start'] = pd.to_datetime(df_runs['start'], errors='coerce')
df_runs['end'] = pd.to_datetime(df_runs['end'], errors='coerce')

# Including the TPU errors in the dataframe
df_runs['tpu_issues'] = ''

# Iterate to find the corresponding errors
for index, run in df_runs.iterrows():
    # Filter issues that occurred during the run
    issues_in_run = df_ers[
        (df_ers['time_cern'] >= run['start']) & (df_ers['time_cern'] <= run['end'])
    ]
    
    # If there are issues, concatenate their information
    if not issues_in_run.empty:
        tpu_issues = issues_in_run.apply(lambda row: f"{row['tpu_number']} ({row['failure_source']})", axis=1)
        df_runs.at[index, 'tpu_issues'] = '; '.join(tpu_issues)


print(df_runs)

                         start                 end  duration tpu_issues
Run Number                                                             
461096     2023-09-19 22:16:00 2023-09-20 08:37:00       610           
461002     2023-09-18 17:12:00 2023-09-19 10:23:00      1037           
460945     2023-09-18 01:18:00 2023-09-18 06:53:00       305           
460944     2023-09-17 15:51:00 2023-09-18 01:08:00       549           
460916     2023-09-17 07:15:00 2023-09-17 09:13:00        61           
...                        ...                 ...       ...        ...
448715     2023-04-08 17:07:00 2023-04-09 17:29:00      1441           
448637     2023-04-07 14:29:00 2023-04-08 01:28:00       610           
448546     2023-04-06 18:07:00 2023-04-06 19:07:00        59           
448543     2023-04-06 16:49:00 2023-04-06 17:56:00        61           
448519     2023-04-06 09:14:00 2023-04-06 14:56:00       305           

[123 rows x 4 columns]


In [24]:
from IPython.display import display
pd.set_option('display.max_rows', None)
pd.set_option('display.max_colwidth', None)

display(df_runs)

start                 end  duration  \
Run Number                                                     
461096     2023-09-19 22:16:00 2023-09-20 08:37:00       610   
461002     2023-09-18 17:12:00 2023-09-19 10:23:00      1037   
460945     2023-09-18 01:18:00 2023-09-18 06:53:00       305   
460944     2023-09-17 15:51:00 2023-09-18 01:08:00       549   
460916     2023-09-17 07:15:00 2023-09-17 09:13:00        61   
460913     2023-09-16 19:45:00 2023-09-17 06:58:00       671   
460860     2023-09-15 13:59:00 2023-09-16 10:21:00      1220   
460837     2023-09-14 21:12:00 2023-09-15 07:43:00       610   
460493     2023-09-11 07:05:00 2023-09-11 15:16:00       488   
460477     2023-09-10 17:19:00 2023-09-11 03:15:00       549   
460447     2023-09-10 06:51:00 2023-09-10 15:09:00       488   
460438     2023-09-09 21:48:00 2023-09-10 00:09:00       122   
460436     2023-09-09 10:22:00 2023-09-09 21:35:00       671   
460348     2023-09-07 13:12:00 2023-09-08 04:17:00       915   
460009     2023-09-01 07:53:00 2023-09-01 16:26:00       488   
456749     2023-07-16 23:25:00 2023-07-17 01:06:00        61   
456729     2023-07-16 08:46:00 2023-07-16 22:33:00       793   
456714     2023-07-15 16:59:00 2023-07-16 07:01:00       854   
456685     2023-07-15 05:46:00 2023-07-15 10:02:00       244   
456665     2023-07-14 20:36:00 2023-07-15 04:02:00       427   
456522     2023-07-14 08:50:00 2023-07-14 10:53:00       122   
456409     2023-07-12 18:42:00 2023-07-13 15:53:00      1281   
456386     2023-07-12 11:48:00 2023-07-12 16:58:00       305   
456346     2023-07-11 23:57:00 2023-07-12 04:05:00       244   
456316     2023-07-11 12:16:00 2023-07-11 21:53:00       549   
456314     2023-07-11 11:10:00 2023-07-11 12:02:00        52   
456303     2023-07-11 08:12:00 2023-07-11 09:43:00        61   
456273     2023-07-10 23:22:00 2023-07-11 06:24:00       427   
456225     2023-07-10 12:35:00 2023-07-10 20:09:00       427   
456164     2023-07-09 20:03:00 2023-07-10 05:44:00       549   
456151     2023-07-09 12:17:00 2023-07-09 17:59:00       305   
456126     2023-07-08 20:45:00 2023-07-09 11:13:00       854   
456118     2023-07-08 05:13:00 2023-07-08 19:45:00       854   
456110     2023-07-07 11:37:00 2023-07-08 03:55:00       976   
456016     2023-07-06 02:19:00 2023-07-06 16:16:00       793   
455975     2023-07-05 10:17:00 2023-07-06 01:09:00       854   
455924     2023-07-04 17:32:00 2023-07-05 08:18:00       854   
455899     2023-07-03 18:06:00 2023-07-04 16:02:00      1281   
455870     2023-07-03 01:11:00 2023-07-03 06:27:00       305   
455857     2023-07-02 17:39:00 2023-07-02 23:31:00       305   
455838     2023-07-02 06:10:00 2023-07-02 12:02:00       305   
455837     2023-07-02 04:12:00 2023-07-02 05:53:00        61   
455818     2023-07-01 19:22:00 2023-07-01 23:56:00       244   
455814     2023-07-01 17:59:00 2023-07-01 19:16:00        61   
455795     2023-07-01 01:30:00 2023-07-01 16:46:00       915   
455702     2023-06-30 08:16:00 2023-06-30 23:17:00       915   
455623     2023-06-28 20:42:00 2023-06-29 23:24:00        61   
455589     2023-06-28 09:38:00 2023-06-28 20:14:00       610   
454322     2023-06-12 23:15:00 2023-06-13 11:09:00       671   
454222     2023-06-11 23:16:00 2023-06-12 11:11:00       671   
454188     2023-06-11 12:32:00 2023-06-11 21:33:00       549   
454163     2023-06-10 23:13:00 2023-06-11 10:57:00       671   
454129     2023-06-10 06:42:00 2023-06-10 19:36:00       732   
454083     2023-06-09 07:52:00 2023-06-10 05:20:00      1281   
454054     2023-06-08 18:31:00 2023-06-09 04:38:00       610   
453981     2023-06-07 22:22:00 2023-06-08 13:51:00       915   
453858     2023-06-07 00:03:00 2023-06-07 11:23:00       671   
453816     2023-06-06 03:36:00 2023-06-06 22:00:00      1098   
453795     2023-06-05 11:49:00 2023-06-06 01:11:00       793   
453754     2023-06-04 20:20:00 2023-06-05 10:11:00       793   
453733     2023-06-04 13:24:00 2023-06-04 19:21:00       

In [42]:
import pandas as pd
import json


ers_folder = "/eos/user/j/jhoya/DAQ/AnomalyDetection/strada/dataset_generation/ers_errors/"
df_ers = pd.read_csv(f"{ers_folder}processed_2023_ERS.csv", parse_dates=True)


# Convert time columns to datetime format. Dates in python are a painnnnnn!!!
df_ers['time_cern'] = pd.to_datetime(df_ers['time_cern'], utc=True, errors='coerce').dt.tz_localize(None)
df_runs['start'] = pd.to_datetime(df_runs['start'], errors='coerce')
df_runs['end'] = pd.to_datetime(df_runs['end'], errors='coerce')

# Create a list to store the JSON representation
runs_list = []

print()

# Iterate over each run and find corresponding issues
for run_number, run in df_runs.iterrows():
    # Filter issues that occurred during the run
    issues_in_run = df_ers[
        (df_ers['time_cern'] >= run['start']) & (df_ers['time_cern'] <= run['end'])
    ]
    
    # Create a dictionary to represent the run
    run_dict = {
        "Run Number": int(run_number),
        "start": run['start'].isoformat(),
        "end": run['end'].isoformat(),
        "duration": int(run['duration']),
        "tpu_issues": []
    }
    
    # Add the corresponding issues to the run
    for _, issue in issues_in_run.iterrows():
        issue_dict = {
            "time": issue['time_cern'].isoformat(),
            "tpu": issue['tpu_number'],
            "failure_source": issue['failure_source']
        }
        run_dict["tpu_issues"].append(issue_dict)

    # Append the run dictionary to the list
    runs_list.append(run_dict)

# Write the list of runs to a JSON file
with open(f'{ers_folder}runs_with_tpu_issues.json', 'w') as json_file:
    json.dump(runs_list, json_file, indent=4)

print("Data has been successfully written to 'runs_with_tpu_issues.json'")






Data has been successfully written to 'runs_with_tpu_issues.json'


# Adding anomaly information from the Clustering algorithm 

Now that we have a json file with all the runs and the tpu issues that we can extract from ERS, we include also any anomalies found by the clustering algorithm. <br/>
We want to do this in order to be able to select a few set of runs with, in principle, no issues (or not drastic at least), that we can use to train the DeepLearning algorithms.


In [ ]:
# Load JSON anomaly data
json_file = f"/eos/user/j/jhoya/DAQ/AnomalyDetection/ML_resources/Strada_parts/results/run_{run_number}.json"

In [46]:
import json
import os

ers_folder = "/eos/user/j/jhoya/DAQ/AnomalyDetection/strada/dataset_generation/ers_errors/"

with open(f'{ers_folder}runs_with_tpu_issues.json', 'r') as json_file:
    runs_data = json.load(json_file)

# Directory where anomaly JSON files are stored
anomalies_dir = '/eos/user/j/jhoya/DAQ/AnomalyDetection/ML_resources/Strada_parts/results/'

# Iterate over each run and add anomaly information if available
for run in runs_data:
    run_number = run["Run Number"]
    anomaly_file = os.path.join(anomalies_dir, f'run_{run_number}.json')

    # Initialize the anomalies key with an empty list
    run["anomalies"] = {}

    # Check if the anomaly JSON file for the current run exists
    if os.path.exists(anomaly_file):
        # Load the anomaly JSON file
        with open(anomaly_file, 'r') as anomaly_json_file:
            anomalies = json.load(anomaly_json_file)

        # Iterate over anomalies to find Clustering anomalies
        for tpu, anomaly_data in anomalies.items():
            for timestamp, details in anomaly_data.items():
                #if any(a in ["ClusteringDropToZero", "ClusteringGeneral"] for a in details["types"]):
                for anomaly_type in details["types"]:
                    if anomaly_type in ["ClusteringDropToZero", "ClusteringGeneral"]:
                        if tpu not in run["anomalies"]:
                            run["anomalies"][tpu] = {}

                        # Ensure the anomaly type exists for the TPU
                        if anomaly_type not in run["anomalies"][tpu]:
                            run["anomalies"][tpu][anomaly_type] = []

                        # Append the relevant information
                        run["anomalies"][tpu][anomaly_type].append({
                            "timestamp": timestamp,
                            "duration": details["duration"]
                        })

# Write the updated runs data to a new JSON file
with open(f'{ers_folder}updated_runs_with_tpu_issues.json', 'w') as updated_json_file:
    json.dump(runs_data, updated_json_file, indent=4)

print("Data has been successfully updated and written to 'updated_runs_with_tpu_issues.json'")


Data has been successfully updated and written to 'updated_runs_with_tpu_issues.json'
